In [1]:
!pip install yfinance
!pip install pandas_ta
!pip install streamlit
!npm install -g localtunnel
import pandas as pd
import numpy as np
import streamlit as st
import yfinance as yf
import plotly.express as px
import plotly.graph_objects as go
import pandas_ta as ta


import warnings
warnings.filterwarnings('ignore')

⠙⠹⠸⠼⠴⠦⠧⠇⠏⠋⠙⠹⠸⠼⠴⠦⠧⠇⠏⠋
changed 22 packages in 4s
⠙
⠙3 packages are looking for funding
⠙  run `npm fund` for details
⠙

In [2]:
def collect_data(ticker_name, start_date, end_date):
    data = yf.download(ticker_name, start_date, end_date, multi_level_index = False)
    data['Ticker'] = ticker_name
    return data

In [3]:
date_started = '2009-01-01'
date_ended = '2024-12-30'

btc = collect_data('BTC-USD', date_started, date_ended)
eth = collect_data('ETH-USD', date_started, date_ended)
usdt = collect_data('USDT-USD', date_started, date_ended)
xrp = collect_data('XRP-USD', date_started, date_ended)
sol = collect_data('SOL-USD', date_started, date_ended)
bnb = collect_data('BNB-USD', date_started, date_ended)
usdc = collect_data('USDC-USD', date_started, date_ended)
doge = collect_data('DOGE-USD', date_started, date_ended)
ada = collect_data('ADA-USD', date_started, date_ended)
trx = collect_data('TRX-USD', date_started, date_ended)

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


In [4]:
df = pd.concat([btc, eth, usdt, xrp, sol, bnb, usdc, doge, ada, trx], axis = 0).reset_index()

In [5]:
df.head()

Date       Close        High         Low        Open    Volume  \
0 2014-09-17  457.334015  468.174011  452.421997  465.864014  21056800   
1 2014-09-18  424.440002  456.859985  413.104004  456.859985  34483200   
2 2014-09-19  394.795990  427.834991  384.532013  424.102997  37919700   
3 2014-09-20  408.903992  423.295990  389.882996  394.673004  36863600   
4 2014-09-21  398.821014  412.425995  393.181000  408.084991  26580100   

    Ticker  
0  BTC-USD  
1  BTC-USD  
2  BTC-USD  
3  BTC-USD  
4  BTC-USD

In [6]:
def macd(data, fast=12, slow=26, signal=9):
    return ta.macd(data['Close'], fast, slow, signal)

def rsi(data, period=14):
    return ta.rsi(data['Close'], period)

def bbands(data, period=5, std=2):
    return ta.bbands(data['Close'], period, std)

def obv(data):
    return ta.obv(data['Close'], data['Volume'])

In [7]:
macd_vals = ta.macd(df['Close']).fillna(0)
df['MACD_12_26_9'], df['MACDh_12_26_9'], df['MACDs_12_26_9'] = macd_vals.values.T

df['RSI_14'] = ta.rsi(df['Close']).fillna(0)

bbands = ta.bbands(df['Close']).fillna(0)
df = df.join(bbands)  # Gabungkan Bollinger Bands ke df

df['OBV'] = obv(df)  # Pastikan OBV tidak error

In [8]:
df.head()

Date       Close        High         Low        Open    Volume  \
0 2014-09-17  457.334015  468.174011  452.421997  465.864014  21056800   
1 2014-09-18  424.440002  456.859985  413.104004  456.859985  34483200   
2 2014-09-19  394.795990  427.834991  384.532013  424.102997  37919700   
3 2014-09-20  408.903992  423.295990  389.882996  394.673004  36863600   
4 2014-09-21  398.821014  412.425995  393.181000  408.084991  26580100   

    Ticker  MACD_12_26_9  MACDh_12_26_9  MACDs_12_26_9  RSI_14   BBL_5_2.0  \
0  BTC-USD           0.0            0.0            0.0     0.0    0.000000   
1  BTC-USD           0.0            0.0            0.0     0.0    0.000000   
2  BTC-USD           0.0            0.0            0.0     0.0    0.000000   
3  BTC-USD           0.0            0.0            0.0     0.0    0.000000   
4  BTC-USD           0.0            0.0            0.0     0.0  371.505935   

    BBM_5_2.0  BBU_5_2.0  BBB_5_2.0  BBP_5_2.0         OBV  
0    0.000000    0.00000   0.000000   0.000000  21056800.0  
1    0.000000    0.00000   0.000000   0.000000 -13426400.0  
2    0.000000    0.00000   0.000000   0.000000 -51346100.0  
3    0.000000    0.00000   0.000000   0.000000 -14482500.0  
4  416.859003  462.21207  21.759428   0.301138 -41062600.0

In [9]:
df['Date'] = pd.to_datetime(df['Date'])

In [10]:
# Ambil daftar unik ticker yang ada dalam dataframe
unique_tickers = df['Ticker'].unique()

# --- Buat Figur Utama ---
fig = go.Figure()

# --- Tambahkan Jenis Chart ---
for ticker in unique_tickers:
    df_ticker = df[df['Ticker'] == ticker]

    fig.add_trace(go.Candlestick(x=df_ticker['Date'], open=df_ticker['Open'], high=df_ticker['High'],
                                 low=df_ticker['Low'], close=df_ticker['Close'],
                                 name=f'Candlestick {ticker}', visible=(ticker == unique_tickers[0])))

    fig.add_trace(go.Scatter(x=df_ticker['Date'], y=df_ticker['Close'], mode='lines',
                             name=f'Line Chart {ticker}', visible=False))

    fig.add_trace(go.Bar(x=df_ticker['Date'], y=df_ticker['Close'],
                         name=f'Bar Chart {ticker}', visible=False))

    fig.add_trace(go.Ohlc(x=df_ticker['Date'], open=df_ticker['Open'], high=df_ticker['High'],
                          low=df_ticker['Low'], close=df_ticker['Close'],
                          name=f'OHLC {ticker}', visible=False))

# --- Dropdown untuk Ticker ---
ticker_dropdown = {
    "buttons": [
        {
            "label": ticker,
            "method": "update",
            "args": [{"visible": [(t == ticker) for t in unique_tickers for _ in range(4)]}],
        }
        for ticker in unique_tickers
    ],
    "direction": "down",
    "showactive": True,
    "x": 0.10,
    "xanchor": "left",
    "y": 1.2,
    "yanchor": "top",
    #"font": {"size": 15, "color": "black"},
    "bgcolor": "white",
    "borderwidth": 2,
}

# --- Dropdown untuk Indikator ---
indicator_dropdown = {
    "buttons": [
        {"label": "None", "method": "update", "args": [{"visible": [True] * 4 + [False] * 5}]},
        {"label": "MACD", "method": "update", "args": [{"visible": [True] * 4 + [True, True, False, False, False]}]},
        {"label": "RSI", "method": "update", "args": [{"visible": [True] * 4 + [False, False, True, False, False]}]},
        {"label": "Bollinger Bands", "method": "update", "args": [{"visible": [True] * 4 + [False, False, False, True, True]}]},
        {"label": "OBV", "method": "update", "args": [{"visible": [True] * 4 + [False, False, False, False, True]}]},
    ],
    "direction": "down",
    "showactive": True,
    "x": 0.7,
    "xanchor": "left",
    "y": 1.2,
    "yanchor": "top",
}

# --- Dropdown untuk Jenis Chart ---
chart_dropdown = {
    "buttons": [
        {"label": "Candlestick", "method": "update", "args": [{"visible": [True, False, False, False]}]},
        {"label": "Line Chart", "method": "update", "args": [{"visible": [False, True, False, False]}]},
        {"label": "Bar Chart", "method": "update", "args": [{"visible": [False, False, True, False]}]},
        {"label": "OHLC", "method": "update", "args": [{"visible": [False, False, False, True]}]},
    ],
    "direction": "down",
    "showactive": True,
    "x": 0.9,
    "xanchor": "left",
    "y": 1.2,
    "yanchor": "top",
}

# --- Tambahkan Button Time Range ---
time_range_buttons = {
    "buttons": [
        {"label": "24h", "method": "relayout", "args": ["xaxis.range", [df['Date'].max() - pd.Timedelta(days=1), df['Date'].max()]]},
        {"label": "7w", "method": "relayout", "args": ["xaxis.range", [df['Date'].max() - pd.Timedelta(weeks=7), df['Date'].max()]]},
        {"label": "1mo", "method": "relayout", "args": ["xaxis.range", [df['Date'].max() - pd.DateOffset(months=1), df['Date'].max()]]},
        {"label": "1yr", "method": "relayout", "args": ["xaxis.range", [df['Date'].max() - pd.DateOffset(years=1), df['Date'].max()]]},
        {"label": "All", "method": "relayout", "args": ["xaxis.range", [df['Date'].min(), df['Date'].max()]]}
    ],
    "direction": "down",
    "x": 0.63,
    "xanchor": "left",
    "y": 1.2,
    "yanchor": "top",
    #"font": {"size": 15, "color": "black"},
    "bgcolor": "white",
    "borderwidth": 2,
}

# --- Update Layout ---
fig.update_layout(
    updatemenus=[ticker_dropdown, indicator_dropdown, chart_dropdown, time_range_buttons],
    title="Crypto Price Visualization",
    xaxis_title="Date",
    yaxis_title="Price",
    xaxis_rangeslider_visible=True
)

# --- Tampilkan Grafik ---
fig.show()


In [11]:
!wget -q -O - ipv4.icanhazip.com

34.82.110.54


In [12]:
%%writefile app.py
import yfinance as yf
import numpy as np
import pandas as pd
import pandas_ta as ta
import plotly.graph_objects as go
import streamlit as st

# Load Data (Gantilah dengan sumber data yang sesuai)
def collect_data(ticker_name, start_date, end_date):
    data = yf.download(ticker_name, start_date, end_date, multi_level_index = False)
    data['Ticker'] = ticker_name
    return data

date_started = '2009-01-01'
date_ended = '2024-12-30'

btc = collect_data('BTC-USD', date_started, date_ended)
eth = collect_data('ETH-USD', date_started, date_ended)
usdt = collect_data('USDT-USD', date_started, date_ended)
xrp = collect_data('XRP-USD', date_started, date_ended)
sol = collect_data('SOL-USD', date_started, date_ended)
bnb = collect_data('BNB-USD', date_started, date_ended)
usdc = collect_data('USDC-USD', date_started, date_ended)
doge = collect_data('DOGE-USD', date_started, date_ended)
ada = collect_data('ADA-USD', date_started, date_ended)
trx = collect_data('TRX-USD', date_started, date_ended)
df = pd.concat([btc, eth, usdt, xrp, sol, bnb, usdc, doge, ada, trx], axis = 0).reset_index()

def macd(data, fast=12, slow=26, signal=9):
    return ta.macd(data['Close'], fast, slow, signal)

def rsi(data, period=14):
    return ta.rsi(data['Close'], period)

def bbands(data, period=5, std=2):
    return ta.bbands(data['Close'], period, std)

def obv(data):
    return ta.obv(data['Close'], data['Volume'])

macd_vals = ta.macd(df['Close']).fillna(0)
df['MACD_12_26_9'], df['MACDh_12_26_9'], df['MACDs_12_26_9'] = macd_vals.values.T

df['RSI_14'] = ta.rsi(df['Close']).fillna(0)

bbands = ta.bbands(df['Close']).fillna(0)
df = df.join(bbands)  # Gabungkan Bollinger Bands ke df

df['OBV'] = obv(df)  # Pastikan OBV tidak error
df['Date'] = pd.to_datetime(df['Date'])  # Pastikan kolom Date dalam format datetime

# Ambil daftar unik ticker
unique_tickers = df['Ticker'].unique()

# Sidebar
st.sidebar.title("Options")
selected_ticker = st.sidebar.selectbox("Select Ticker", unique_tickers)
chart_type = st.sidebar.selectbox("Select Chart Type", ["Candlestick", "Line Chart", "Bar Chart", "OHLC"])
indicator = st.sidebar.selectbox("Select Indicator", ["None", "MACD", "RSI", "Bollinger Bands", "OBV"])
time_range = st.sidebar.radio("Select Time Range", ["24h", "7w", "1mo", "1yr", "All"])

# Filter data berdasarkan ticker
df_ticker = df[df['Ticker'] == selected_ticker]

# Buat Figur
fig = go.Figure()

# Tambahkan Chart
if chart_type == "Candlestick":
    fig.add_trace(go.Candlestick(x=df_ticker['Date'], open=df_ticker['Open'], high=df_ticker['High'],
                                 low=df_ticker['Low'], close=df_ticker['Close'], name=f'Candlestick {selected_ticker}'))
elif chart_type == "Line Chart":
    fig.add_trace(go.Scatter(x=df_ticker['Date'], y=df_ticker['Close'], mode='lines', name=f'Line Chart {selected_ticker}'))
elif chart_type == "Bar Chart":
    fig.add_trace(go.Bar(x=df_ticker['Date'], y=df_ticker['Close'], name=f'Bar Chart {selected_ticker}'))
elif chart_type == "OHLC":
    fig.add_trace(go.Ohlc(x=df_ticker['Date'], open=df_ticker['Open'], high=df_ticker['High'],
                          low=df_ticker['Low'], close=df_ticker['Close'], name=f'OHLC {selected_ticker}'))

# Tambahkan Indikator
if indicator == "MACD":
    fig.add_trace(go.Scatter(x=df_ticker['Date'], y=df_ticker['MACD_12_26_9'], mode='lines', name='MACD'))
    fig.add_trace(go.Scatter(x=df_ticker['Date'], y=df_ticker['MACDs_12_26_9'], mode='lines', name='Signal Line'))
elif indicator == "RSI":
    fig.add_trace(go.Scatter(x=df_ticker['Date'], y=df_ticker['RSI_14'], mode='lines', name='RSI'))
elif indicator == "Bollinger Bands":
    fig.add_trace(go.Scatter(x=df_ticker['Date'], y=df_ticker['BBL_5_2.0'], mode='lines', name='Lower Band'))
    fig.add_trace(go.Scatter(x=df_ticker['Date'], y=df_ticker['BBU_5_2.0'], mode='lines', name='Upper Band'))
elif indicator == "OBV":
    fig.add_trace(go.Scatter(x=df_ticker['Date'], y=df_ticker['OBV'], mode='lines', name='OBV'))

# Atur Time Range
if time_range == "24h":
    fig.update_xaxes(range=[df_ticker['Date'].max() - pd.Timedelta(days=1), df_ticker['Date'].max()])
elif time_range == "7w":
    fig.update_xaxes(range=[df_ticker['Date'].max() - pd.Timedelta(weeks=7), df_ticker['Date'].max()])
elif time_range == "1mo":
    fig.update_xaxes(range=[df_ticker['Date'].max() - pd.DateOffset(months=1), df_ticker['Date'].max()])
elif time_range == "1yr":
    fig.update_xaxes(range=[df_ticker['Date'].max() - pd.DateOffset(years=1), df_ticker['Date'].max()])
else:
    fig.update_xaxes(range=[df_ticker['Date'].min(), df_ticker['Date'].max()])

# Update Layout
fig.update_layout(title="Crypto Price Visualization", xaxis_title="Date", yaxis_title="Price", xaxis_rangeslider_visible=True)

# Tampilkan Grafik
st.plotly_chart(fig)


Overwriting app.py


In [13]:
!streamlit run app.py & npx localtunnel --port 8501



⠙⠹⠸⠼
  You can now view your Streamlit app in your browser.

  Local URL: http://localhost:8501
  Network URL: http://172.28.0.12:8501
  External URL: http://34.82.110.54:8501

⠴⠦⠧⠇your url is: https://real-pugs-clean.loca.lt
  Stopping...
^C
